In [1]:
from astropy.table import Table
from astropy import log
log.setLevel('WARNING')

### Premiers exemples

In [2]:
table1 = Table([[0.0, 1.0, 2.0, 3.0], ["un", "deux", "trois", "quatre"]], names=("value", "name"))
print (table1)
print (table1["value"])
print (table1[0])

value  name 
----- ------
  0.0     un
  1.0   deux
  2.0  trois
  3.0 quatre
value
-----
  0.0
  1.0
  2.0
  3.0
value name
----- ----
  0.0   un


#### ajouter/supprimer des colonnes

In [3]:
from astropy.table import Column

newcol = Column([1.1, 3.3, 5., 0.], name="newcol")
table1.add_column(newcol)
table1.remove_column("name")
print (table1)

value newcol
----- ------
  0.0    1.1
  1.0    3.3
  2.0    5.0
  3.0    0.0


#### Aggregation des 2 tables

In [4]:
table2 = Table([[1,2,3,4], [1.1, None, None,0]], 
               names=("col1", "col2"))

matable = Table([table1["value"], table1["newcol"], table2["col1"], table2["col2"]])
print (matable)

value newcol col1 col2
----- ------ ---- ----
  0.0    1.1    1  1.1
  1.0    3.3    2 None
  2.0    5.0    3 None
  3.0    0.0    4    0


#### modification des valeurs

In [5]:
table1["value"] *=2
print (table1)
print (matable) # matable n'est pas modifiee

matable["value"] *=2
print (matable)

value newcol
----- ------
  0.0    1.1
  2.0    3.3
  4.0    5.0
  6.0    0.0
value newcol col1 col2
----- ------ ---- ----
  0.0    1.1    1  1.1
  1.0    3.3    2 None
  2.0    5.0    3 None
  3.0    0.0    4    0
value newcol col1 col2
----- ------ ---- ----
  0.0    1.1    1  1.1
  2.0    3.3    2 None
  4.0    5.0    3 None
  6.0    0.0    4    0


###  import des tables VizieR LSPM limite a 500 records
le format choisit dans l'exemple est VOTable, mais TSV, FITS sont aussi disponibles!

In [6]:
tab = Table.read("http://vizier.u-strasbg.fr/viz-bin/votable?-source=I/298/lspm_n&-out.max=500")
print (tab[0:5])

   LSPM     NLTT   USNO-B1     RAJ2000    DEJ2000       pm    Aflag Vemag   V-J 
                                 deg        deg     arcs / yr        mag    mag 
---------- ----- ------------ ---------- ---------- --------- ----- ------ -----
J0000+0003 58703 0900-0000025   0.075275   0.056054     0.253     S  15.02  3.27
J0000+0041 58724 0906-0000116   0.129708   0.685727     0.198     S  16.31  3.70
J0000+0313 58739 0932-0000102   0.168501   3.228500     0.352     S  17.43  3.72
J0000+0356 58690 0939-0000011   0.018693   3.946458     0.227     A  12.39  2.58
J0000+0409    -- 0941-0000118   0.211799   4.162965     0.170     T  11.71  1.78


#### Affichage des header

In [7]:
#tab["V-J"].info() -- devrait fonctionner!!!!
print (tab["V-J"].meta)
print (tab["V-J"].description)

OrderedDict([('width', 5), ('precision', '2'), ('values', {'null': nan})])
? Estimated V-J color (10)


#### Affichage dans une page web

In [8]:
tab.show_in_browser(jsviewer=True) 

#### ajouter des metadonnees

In [9]:
print (tab["V-J"].meta)

tab["V-J"].meta["madescription"]="color Vmag - Jmag"
print (tab["V-J"].meta)

OrderedDict([('width', 5), ('precision', '2'), ('values', {'null': nan})])
OrderedDict([('width', 5), ('precision', '2'), ('values', {'null': nan}), ('madescription', 'color Vmag - Jmag')])


#### Utiliser les UCD
exemple Gaia mag autour d'une position 0+0

In [10]:
from astropy.io.votable import parse
votable = parse("http://vizier.u-strasbg.fr/viz-bin/votable?-source=I/345/gaia2&-c=0+0")

In [11]:
table = votable.get_first_table()
print (table)

    RA_ICRS     e_RA_ICRS     DE_ICRS     ... E_BP-RP_  Rad      Lum   
      deg          mas          deg       ...   mag     Rsun     Lsun  
--------------- --------- --------------- ... -------- ------ ---------
  0.02145651484    0.3235  -0.02379344308 ...       --     --        --
359.99991940236    0.2838  -0.03288657521 ...       --     --        --
359.99984304906    9.4457  -0.03302463598 ...       --     --        --
  0.00943770097    0.3457  -0.00089373642 ...       --     --        --
  0.03064536408    0.0475  -0.00627903258 ...   0.0053   0.77     0.433
359.98003807419    0.3504   0.00788634506 ...       --     --        --
359.98197003637    0.2322  -0.00428806972 ...       --     --        --
359.97755696462    0.8966   0.00208200929 ...       --     --        --
359.98956505150    0.0535   0.01222220565 ...   0.0230   0.65     0.216
359.98936001231    0.1096   0.02766082458 ...       --     --        --


In [12]:
for field in table.fields:
    print("column {:20s}: ucd={}".format(field.name, field.ucd))

column RA_ICRS             : ucd=pos.eq.ra;meta.main
column e_RA_ICRS           : ucd=stat.error;pos.eq.ra
column DE_ICRS             : ucd=pos.eq.dec;meta.main
column e_DE_ICRS           : ucd=stat.error;pos.eq.dec
column Source              : ucd=meta.id;meta.main
column Plx                 : ucd=pos.parallax
column e_Plx               : ucd=stat.error;pos.parallax
column pmRA                : ucd=pos.pm;pos.eq.ra
column e_pmRA              : ucd=stat.error;pos.pm;pos.eq.ra
column pmDE                : ucd=pos.pm;pos.eq.dec
column e_pmDE              : ucd=stat.error;pos.pm;pos.eq.dec
column Dup                 : ucd=meta.code.status
column FG                  : ucd=phot.flux;stat.mean;em.opt
column e_FG                : ucd=stat.error;phot.flux;stat.mean
column Gmag                : ucd=phot.mag;stat.mean;em.opt
column e_Gmag              : ucd=stat.error;phot.mag;stat.mean
column FBP                 : ucd=phot.flux;stat.mean;em.opt.B
column e_FBP               : ucd=stat.error;phot

In [13]:
def get_ucd(table, ucd):
    cols = []
    for field in table.fields:
        if field.ucd.find(ucd)>-1:
            cols.append(field)
    return cols

In [14]:
magcols = get_ucd(table,"phot.mag")
for rec in table.array:
    s = "({},{}):".format(rec["RA_ICRS"], rec["DE_ICRS"])
    for i in range(len(magcols)):
        s += " {}={} ({})".format(magcols[i].name, rec[i], magcols[i].ucd)
    print (s)

(0.02145651484,-0.02379344308): Gmag=0.02145651484 (phot.mag;stat.mean;em.opt) e_Gmag=0.3235 (stat.error;phot.mag;stat.mean) BPmag=-0.02379344308 (phot.mag;stat.mean;em.opt.B) e_BPmag=0.1677 (stat.error;phot.mag;stat.mean) RPmag=2449957888052139648 (phot.mag;stat.mean;em.opt.R) e_RPmag=0.2545 (stat.error;phot.mag;stat.mean)
(359.99991940236,-0.03288657521): Gmag=359.99991940236 (phot.mag;stat.mean;em.opt) e_Gmag=0.2838 (stat.error;phot.mag;stat.mean) BPmag=-0.03288657521 (phot.mag;stat.mean;em.opt.B) e_BPmag=0.1557 (stat.error;phot.mag;stat.mean) RPmag=2449958064145765376 (phot.mag;stat.mean;em.opt.R) e_RPmag=2.4592 (stat.error;phot.mag;stat.mean)
(359.99984304906,-0.03302463598): Gmag=359.99984304906 (phot.mag;stat.mean;em.opt) e_Gmag=9.4457 (stat.error;phot.mag;stat.mean) BPmag=-0.03302463598 (phot.mag;stat.mean;em.opt.B) e_BPmag=1.6573 (stat.error;phot.mag;stat.mean) RPmag=2449958064146999808 (phot.mag;stat.mean;em.opt.R) e_RPmag=-- (stat.error;phot.mag;stat.mean)
(0.00943770097,-0.

### Faire une selection avec numpy
#### colonne "V-J" <2

In [15]:
import numpy as np
ind = np.where(tab["V-J"]<2)
print (tab[ind])

    LSPM     NLTT   USNO-B1     RAJ2000   ...     pm    Aflag Vemag   V-J 
                                  deg     ... arcs / yr        mag    mag 
----------- ----- ------------ ---------- ... --------- ----- ------ -----
 J0000+0409    -- 0941-0000118   0.211799 ...     0.170     T  11.71  1.78
 J0000+1659 58751 1069-0000132   0.200457 ...     0.313     T   8.80  1.85
 J0000+1758 58731 1079-0000209   0.152583 ...     0.365     T  10.60  1.98
 J0000+1906    -- 1091-0000108   0.120978 ...     0.163     S  18.90  0.04
 J0000+2002 58692 1100-0000025   0.022002 ...     0.288     T   9.48  1.46
 J0000+3411 58691 1241-0000033   0.017026 ...     0.236     T   8.50  1.25
 J0000+3531    -- 1255-0000040   0.035142 ...     0.182     T  12.59  1.60
 J0000+3545    -- 1257-0000228   0.222362 ...     0.167     T  10.00  1.96
 J0000+3902 58700 1290-0000077   0.063290 ...     0.227     T  10.71  1.45
 J0000+4312 58705 1332-0000149   0.079543 ...     0.212     T  11.65  1.73
        ...   ...        

/usr/lib64/python3.4/site-packages/astropy/table/column.py:928: RuntimeWarning: invalid value encountered in less
  return getattr(self.data, oper)(other)


### modifier les unites
#### colonne "V-J" en mmag

In [16]:
from astropy import units as u

tab["V-J"].convert_unit_to(u.mmag)
print (tab)

   LSPM     NLTT   USNO-B1     RAJ2000   ...     pm    Aflag Vemag    V-J  
                                 deg     ... arcs / yr        mag     mmag 
---------- ----- ------------ ---------- ... --------- ----- ------ -------
J0000+0003 58703 0900-0000025   0.075275 ...     0.253     S  15.02 3270.00
J0000+0041 58724 0906-0000116   0.129708 ...     0.198     S  16.31 3700.00
J0000+0313 58739 0932-0000102   0.168501 ...     0.352     S  17.43 3720.00
J0000+0356 58690 0939-0000011   0.018693 ...     0.227     A  12.39 2580.00
J0000+0409    -- 0941-0000118   0.211799 ...     0.170     T  11.71 1780.00
J0000+0812    -- 0982-0000215   0.219538 ...     0.185     S  18.86 2980.00
J0000+0852 58753 0988-0000105   0.211180 ...     0.231     S  16.57 3790.00
J0000+1121 58688 1013-0000009   0.015681 ...     0.183     S  16.86 2270.00
J0000+1348 58687 1038-0000015   0.022462 ...     0.232     S  16.37 4040.00
J0000+1353    -- 1038-0000126   0.188751 ...     0.183     S  16.78 4270.00
       ...  

/usr/lib64/python3.4/site-packages/astropy/table/column.py:618: MaskedArrayFutureWarning: setting an item on a masked array which has a shared mask will not copy the mask and also change the original mask array in the future.
Check the NumPy 1.11 release notes for more information.
  new_unit, self.data, equivalencies=equivalencies)


### Ajout de colonnes en Galactique

In [17]:
from astropy.coordinates import SkyCoord

pos = SkyCoord(tab["RAJ2000"], tab["DEJ2000"], frame='icrs')
print (pos.to_string('hmsdms')[:3])

gal = pos.transform_to('galactic')

#tab.remove_column("l")
#tab.remove_column("b")
tab.add_column(Column(gal.l, name="l"))
tab.add_column(Column(gal.b, name="b"))

print (tab[:3])

['00h00m18.066s +00d03m21.7944s', '00h00m31.1299s +00d41m08.6172s', '00h00m40.4402s +03d13m42.6s']
   LSPM     NLTT   USNO-B1    ...   V-J         l             b       
                              ...   mmag       deg           deg      
---------- ----- ------------ ... ------- ------------- --------------
J0000+0003 58703 0900-0000025 ... 3270.00 96.5209629243 -60.1670035914
J0000+0041 58724 0906-0000116 ... 3700.00 97.1124909892 -59.6089812288
J0000+0313 58739 0932-0000102 ... 3720.00  99.001127599  -57.265648543


### Masque sur des colonnes
#### on met a null les valeurs de la colonnes Vemag <15

In [18]:
from astropy.table import MaskedColumn

b = MaskedColumn(tab["Vemag"], mask=tab["Vemag"]<15, name="Vemag")
tab.remove_column("Vemag")
tab.add_column(b)

print (tab[:10])

   LSPM     NLTT   USNO-B1     RAJ2000   ...       l             b        Vemag 
                                 deg     ...      deg           deg        mag  
---------- ----- ------------ ---------- ... ------------- -------------- ------
J0000+0003 58703 0900-0000025   0.075275 ... 96.5209629243 -60.1670035914  15.02
J0000+0041 58724 0906-0000116   0.129708 ... 97.1124909892 -59.6089812288  16.31
J0000+0313 58739 0932-0000102   0.168501 ...  99.001127599  -57.265648543  17.43
J0000+0356 58690 0939-0000011   0.018693 ... 99.2192525065 -56.5420234981     --
J0000+0409    -- 0941-0000118   0.211799 ... 99.6845915004 -56.4081323611     --
J0000+0812    -- 0982-0000215   0.219538 ... 102.043116098 -52.5966966396  18.86
J0000+0852 58753 0988-0000105   0.211180 ... 102.378684721 -51.9595456817  16.57
J0000+1121 58688 1013-0000009   0.015681 ... 103.307483848 -49.5410120877  16.86
J0000+1348 58687 1038-0000015   0.022462 ... 104.410371555 -47.2165500041  16.37
J0000+1353    -- 1038-000012

/usr/lib64/python3.4/site-packages/astropy/table/column.py:928: RuntimeWarning: invalid value encountered in less
  return getattr(self.data, oper)(other)


#### mettre une valeur par defaut pour le valeurs nulles

In [19]:
tab["Vemag"].fill_value = 99.99
print (tab.filled()[:10])

   LSPM     NLTT    USNO-B1    ...       l             b        Vemag 
                               ...      deg           deg        mag  
---------- ------ ------------ ... ------------- -------------- ------
J0000+0003  58703 0900-0000025 ... 96.5209629243 -60.1670035914  15.02
J0000+0041  58724 0906-0000116 ... 97.1124909892 -59.6089812288  16.31
J0000+0313  58739 0932-0000102 ...  99.001127599  -57.265648543  17.43
J0000+0356  58690 0939-0000011 ... 99.2192525065 -56.5420234981  99.99
J0000+0409 999999 0941-0000118 ... 99.6845915004 -56.4081323611  99.99
J0000+0812 999999 0982-0000215 ... 102.043116098 -52.5966966396  18.86
J0000+0852  58753 0988-0000105 ... 102.378684721 -51.9595456817  16.57
J0000+1121  58688 1013-0000009 ... 103.307483848 -49.5410120877  16.86
J0000+1348  58687 1038-0000015 ... 104.410371555 -47.2165500041  16.37
J0000+1353 999999 1038-0000126 ... 104.675946125 -47.1775200567  16.78


### sauvegarde du resultat au format CDS

In [20]:
tab.write("matable.ascii", format="ascii.fixed_width")

#### Retour aux valeurs d'origines

In [21]:
tab.mask = False
print (tab[:10])

   LSPM        NLTT      USNO-B1    ...       l             b        Vemag 
                                    ...      deg           deg        mag  
---------- ----------- ------------ ... ------------- -------------- ------
J0000+0003       58703 0900-0000025 ... 96.5209629243 -60.1670035914  15.02
J0000+0041       58724 0906-0000116 ... 97.1124909892 -59.6089812288  16.31
J0000+0313       58739 0932-0000102 ...  99.001127599  -57.265648543  17.43
J0000+0356       58690 0939-0000011 ... 99.2192525065 -56.5420234981  12.39
J0000+0409 -2147483648 0941-0000118 ... 99.6845915004 -56.4081323611  11.71
J0000+0812 -2147483648 0982-0000215 ... 102.043116098 -52.5966966396  18.86
J0000+0852       58753 0988-0000105 ... 102.378684721 -51.9595456817  16.57
J0000+1121       58688 1013-0000009 ... 103.307483848 -49.5410120877  16.86
J0000+1348       58687 1038-0000015 ... 104.410371555 -47.2165500041  16.37
J0000+1353 -2147483648 1038-0000126 ... 104.675946125 -47.1775200567  16.78
